In [1]:
import pandas as pd
import numpy as np
from datetime import datetime
import warnings
warnings.simplefilter(action='ignore', category=pd.errors.PerformanceWarning)

pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)

# Read in the biochem, haem and urine data and do some initial processing

In [2]:
data_dir = '../Data/big_cats/Access_DB_table_exports/'
biochem = pd.read_excel(data_dir + 'Biochemistry ReportsTZ_ZV_WA_SA_MG_DM.xlsx')
biochem['Date'] = pd.to_datetime(biochem['Date'])
biochem['ARKS No'] = biochem['ARKS Number']
biochem.drop('ARKS Number', axis = 1, inplace=True)
biochem['biochem id'] = biochem.index # add an id column

haem = pd.read_excel(data_dir + 'Haematology ReportsTZ_ZV_MG.xlsx')
haem['Date'] = pd.to_datetime(haem['Date'])
haem['haem id'] = haem.index  # add an id column

urine = pd.read_excel(data_dir + 'UrinalysisTZ_ZV_WA_SA_MG_DM.xlsx')
urine['Date of Sample Analysis'] = pd.to_datetime(urine['Date of Sample Analysis'])
urine['Date'] = urine['Date of Sample Analysis']
urine.drop('Date of Sample Analysis', axis = 1, inplace=True)
urine['urine id'] = urine.index  # add an id column

In [3]:
print('Biochemistry data has ' + str(len(biochem)) + ' records for ' + str(len(biochem['ARKS No'].unique())) + ' cats')
print('Haematology data has ' + str(len(haem)) + ' records for ' + str(len(haem['ARKS No'].unique())) + ' cats')
print('Urine data has ' + str(len(urine)) + ' records for ' + str(len(urine['ARKS No'].unique())) + ' cats')

Biochemistry data has 1658 records for 330 cats
Haematology data has 727 records for 151 cats
Urine data has 1240 records for 241 cats


In [4]:
# Drop records where ARKS Number or Date is nan
biochem.dropna(subset=['ARKS No', 'Date'], inplace = True)
haem.dropna(subset=['ARKS No', 'Date'], inplace = True)
urine.dropna(subset=['ARKS No', 'Date'], inplace = True)

print('After removing rows records where ARKS Number or Date were nan:')
print('Biochemistry data has ' + str(len(biochem)) + ' records for ' + str(len(biochem['ARKS No'].unique())) + ' cats')
print('Haematology data has ' + str(len(haem)) + ' records for ' + str(len(haem['ARKS No'].unique())) + ' cats')
print('Urine data has ' + str(len(urine)) + ' records for ' + str(len(urine['ARKS No'].unique())) + ' cats')

After removing rows records where ARKS Number or Date were nan:
Biochemistry data has 1658 records for 330 cats
Haematology data has 724 records for 150 cats
Urine data has 1238 records for 240 cats


## add a prefix to each column name to identify which sheet it belongs to
## BUT NOT Date , ARKS No or id bc this is used for the merge

In [5]:
biochem_cols = list(biochem.columns)
biochem_cols.remove('Date')
biochem_cols.remove('ARKS No')
biochem_cols.remove('biochem id')
biochem_dict= {}
for col in biochem_cols:
    biochem_dict[col] = 'biochem: ' + col
# use dictionary to rename columns
biochem.rename(columns = biochem_dict, inplace=True)


haem_cols = list(haem.columns)
haem_cols.remove('Date')
haem_cols.remove('ARKS No')
haem_cols.remove('haem id')
haem_dict= {}
for col in haem_cols:
    haem_dict[col] = 'haem: ' + col
# use dictionary to rename columns
haem.rename(columns = haem_dict, inplace=True)

urine_cols = list(urine.columns)
urine_cols.remove('Date')
urine_cols.remove('ARKS No')
urine_cols.remove('urine id')
urine_dict= {}
for col in urine_cols:
    urine_dict[col] = 'urine: ' + col
# use dictionary to rename columns
urine.rename(columns = urine_dict, inplace=True)

### order is important for the merging

In [6]:
# do some important stuff
haem = haem.sort_values(by=['Date'])
biochem = biochem.sort_values(by=['Date'])
urine = urine.sort_values(by=['Date'])
# add additional cols to keep track of dates from each table
biochem['biochem date'] = biochem['Date']
haem['haem date'] = haem['Date']
urine['urine date'] = urine['Date']

# throw away duplicate dates - keep only the last rrecord
haem.drop_duplicates(subset=['ARKS No', 'Date'], keep='last', inplace=True)
biochem.drop_duplicates(subset=['ARKS No', 'Date'], keep='last', inplace=True)
urine.drop_duplicates(subset=['ARKS No', 'Date'], keep='last', inplace=True)

# Begin merge

## First find the triples

In [7]:
tol = pd.Timedelta('14 day')

# first join haem and biochem
df1 = pd.merge_asof(by=['ARKS No'], left=haem,right=biochem, left_on='Date', right_on='Date', direction='nearest',tolerance=tol)
# then join this to urine
df2 = pd.merge_asof(by=['ARKS No'], left=df1,right=urine, left_on='Date', right_on='Date', direction='nearest',tolerance=tol)

# take only triple matches
triples = df2.dropna(subset=['haem date', 'biochem date', 'urine date'], how='any')
print('there are ' +str(len(triples)) + ' triple matches' )
triples

there are 244 triple matches


haem: ID ARKS No haem: Animal Name       Date haem: Laboratory Report No  \
15        464  670005           Quintus 1988-05-08                        NaN   
16        463  670005           Quintus 1988-05-20                        NaN   
17        462  670005           Quintus 1988-05-25                        NaN   
19        388  750011             X-Ray 1989-03-07                        NaN   
25        551  A20046            Ovambo 1989-09-29                        NaN   
26        547  A20047            Nakuru 1989-09-29                        NaN   
28        470  880014          Claudius 1989-11-24                        NaN   
29        135  880014          Claudius 1989-11-28                        NaN   
30        389  750011             X-Ray 1990-05-31                        NaN   
31        390  750011             X-Ray 1990-07-24                        NaN   
42        327  930228             Kutch 1991-01-11                        NaN   
46        326  930228             Kutch 1991-01-26                        NaN   
47        414  850007               Gus 1991-04-25                        NaN   
51        648  820029             Kashi 1991-07-05                        NaN   
60        164     pet             Rajah 1992-02-27                        NaN   
61        382  730023            Robert 1992-03-17                        NaN   
62        415  850007               Gus 1992-04-24                        NaN   
64        459  910080             Kecil 1992-07-06                        498   
72        404  790036               Ali 1993-01-28                        NaN   
76        408  890000            Audrey 1993-08-06                        NaN   
81        409  890000            Audrey 1993-09-29                        NaN   
84        416  850007               Gus 1994-02-01                        NaN   
85        417  850007               Gus 1994-02-02                        NaN   
89        460  850083             Shiva 1994-09-14                        790   
90        282  920185           Chester 1994-09-28                        NaN   
91        652  820029             Kashi 1994-10-18                        NaN   
96        455  930431             Nonah 1995-04-04                        NaN   
98         79  920260              Nugy 1995-06-13                        578   
100        54  900485             Omaha 1995-08-28                        867   
104       274  850083             Shiva 1995-09-20                        NaN   
106       643  921430              Chad 1995-10-26                        NaN   
132       406  790036               Ali 1996-07-18                        652   
133       607  800015              Chae 1996-08-20                 96-2763713   
134       206  890000            Audrey 1996-09-02                        NaN   
135       207  890000            Audrey 1996-09-09                        NaN   
143        80  920260              Nugy 1996-11-08                        981   
146        56  900485             Omaha 1997-01-08                     015/97   
153        57  900485             Omaha 1997-05-14                        452   
158        12  930229       Indira Maha 1997-09-04                        NaN   
161       544  A20047            Nakuru 1997-10-10                 97-4221224   
167       431  950077             Sarge 1998-02-20                        NaN   
173       208  890000            Audrey 1998-04-08                        NaN   
174        89  980123            Fiddle 1998-04-23                        NaN   
176       209  890000            Audrey 1998-05-29                        NaN   
177       357  870008             Tsavo 1998-06-05                        NaN   
179       429  950077             Sarge 1998-06-09                        NaN   
180       356  870008             Tsavo 1998-06-09                        NaN   
185       355  870008             Tsavo 1998-07-07                        NaN   
195       354  870008             Ts

In [8]:
# get the bichem, haem and urine ids form the triple matches so that they can be removed
triple_haem_ids = list(triples['haem id'])
triple_biochem_ids = list(triples['biochem id'])
triple_urine_ids = list(triples['urine id'])

# drop these ids from original data frames
haem_drop_triple = haem[~haem['haem id'].isin(triple_haem_ids)]
biochem_drop_triple = biochem[~biochem['biochem id'].isin(triple_biochem_ids)]
urine_drop_triple = urine[~urine['urine id'].isin(triple_urine_ids)]

## Now find the doubles

In [9]:
# perform 3 merge combinations
df_hb = pd.merge_asof(by=['ARKS No'], left=haem_drop_triple,right=biochem_drop_triple, left_on='Date', right_on='Date', direction='nearest',tolerance=tol)

df_hu = pd.merge_asof(by=['ARKS No'], left=haem_drop_triple,right=urine_drop_triple, left_on='Date', right_on='Date', direction='nearest',tolerance=tol)

df_ub = pd.merge_asof(by=['ARKS No'], left=urine_drop_triple,right=biochem_drop_triple, left_on='Date', right_on='Date', direction='nearest',tolerance=tol)                 

In [10]:
# take only double matches
double_hb = df_hb.dropna(subset=['haem date', 'biochem date'], how='any')
double_hu = df_hu.dropna(subset=['haem date', 'urine date'], how='any')
double_ub = df_ub.dropna(subset=['urine date', 'biochem date'], how='any')

# get ids for all combos
double_hb_h_ids = list(double_hb['haem id'])
double_hb_b_ids = list(double_hb['biochem id'])

double_hu_h_ids = list(double_hu['haem id'])
double_hu_u_ids = list(double_hu['urine id'])

double_ub_u_ids = list(double_ub['urine id'])
double_ub_b_ids = list(double_ub['biochem id'])

# drop these ids from data frames where triples have already been dropped
haem_singles = haem_drop_triple[~haem_drop_triple['haem id'].isin(double_hb_h_ids + double_hu_h_ids)]
biochem_singles = biochem_drop_triple[~biochem_drop_triple['biochem id'].isin(double_hb_b_ids + double_ub_b_ids)]
urine_singles = urine_drop_triple[~urine_drop_triple['urine id'].isin(double_hu_u_ids + double_ub_u_ids)]

In [11]:
# now concat everything
everything = pd.concat([triples, double_hb, double_hu, double_ub, haem_singles, biochem_singles, urine_singles], sort=False)

In [12]:
everything

haem: ID ARKS No haem: Animal Name       Date  \
15       464.0  670005           Quintus 1988-05-08   
16       463.0  670005           Quintus 1988-05-20   
17       462.0  670005           Quintus 1988-05-25   
19       388.0  750011             X-Ray 1989-03-07   
25       551.0  A20046            Ovambo 1989-09-29   
26       547.0  A20047            Nakuru 1989-09-29   
28       470.0  880014          Claudius 1989-11-24   
29       135.0  880014          Claudius 1989-11-28   
30       389.0  750011             X-Ray 1990-05-31   
31       390.0  750011             X-Ray 1990-07-24   
42       327.0  930228             Kutch 1991-01-11   
46       326.0  930228             Kutch 1991-01-26   
47       414.0  850007               Gus 1991-04-25   
51       648.0  820029             Kashi 1991-07-05   
60       164.0     pet             Rajah 1992-02-27   
61       382.0  730023            Robert 1992-03-17   
62       415.0  850007               Gus 1992-04-24   
64       459.0  910080             Kecil 1992-07-06   
72       404.0  790036               Ali 1993-01-28   
76       408.0  890000            Audrey 1993-08-06   
81       409.0  890000            Audrey 1993-09-29   
84       416.0  850007               Gus 1994-02-01   
85       417.0  850007               Gus 1994-02-02   
89       460.0  850083             Shiva 1994-09-14   
90       282.0  920185           Chester 1994-09-28   
91       652.0  820029             Kashi 1994-10-18   
96       455.0  930431             Nonah 1995-04-04   
98        79.0  920260              Nugy 1995-06-13   
100       54.0  900485             Omaha 1995-08-28   
104      274.0  850083             Shiva 1995-09-20   
106      643.0  921430              Chad 1995-10-26   
132      406.0  790036               Ali 1996-07-18   
133      607.0  800015              Chae 1996-08-20   
134      206.0  890000            Audrey 1996-09-02   
135      207.0  890000            Audrey 1996-09-09   
143       80.0  920260              Nugy 1996-11-08   
146       56.0  900485             Omaha 1997-01-08   
153       57.0  900485             Omaha 1997-05-14   
158       12.0  930229       Indira Maha 1997-09-04   
161      544.0  A20047            Nakuru 1997-10-10   
167      431.0  950077             Sarge 1998-02-20   
173      208.0  890000            Audrey 1998-04-08   
174       89.0  980123            Fiddle 1998-04-23   
176      209.0  890000            Audrey 1998-05-29   
177      357.0  870008             Tsavo 1998-06-05   
179      429.0  950077             Sarge 1998-06-09   
180      356.0  870008             Tsavo 1998-06-09   
185      355.0  870008             Tsavo 1998-07-07   
195      354.0  870008             Tsavo 1998-10-24   
197      180.0  950078              Dani 1998-10-30   
200      147.0  A30035           Selatan 1998-12-15   
202      432.0  950077             Sarge 1999-01-11   
204      426.0  950077             Sarge 1999-01-19   
205      425.0  950077             Sarge 1999-02-02   
206      424.0  950077             Sarge 1999-02-09   
207      197.0  950075            Zenith 1999-02-12   
213      353.0  870008             Tsavo 1999-05-31   
215      285.0  920185           Chester 1999-06-16   
221       65.0  930430             Samar 1999-08-12   
223      286.0  920185           Chester 1999-09-15   
224      287.0  920185           Chester 1999-09-17   
225      445.0  900484           Prafula 1999-12-08   
229      640.0  921430              Chad 2000-03-28   
231      639.0  921430              Chad 2000-04-26   
232      288.0  920185           Chester 2000-05-05   
233      290.0  920185           Chester 2000-06-26   
234      291.0  920185           Chester 2000-07-21   
235      275.0  850083             Shiva 2000-07-24   
236      352.0  870008             Tsavo 2000-07-28   
237      351.0  870008             Tsavo 2000-08-21   
238      350.0  870008             Tsavo 2000-08-25   
243       60.0  900485             Omaha 2000-

In [17]:
# add colums that show the date differences
everything['haem biochem date diff'] = abs(everything['haem date'] - everything['biochem date'])
everything['haem urine date diff'] = abs(everything['haem date'] - everything['urine date'])
everything['urine biochem date diff'] = abs(everything['urine date'] - everything['biochem date'])
everything.head()

haem: ID ARKS No haem: Animal Name       Date haem: Laboratory Report No  \
15     464.0  670005           Quintus 1988-05-08                        NaN   
16     463.0  670005           Quintus 1988-05-20                        NaN   
17     462.0  670005           Quintus 1988-05-25                        NaN   
19     388.0  750011             X-Ray 1989-03-07                        NaN   
25     551.0  A20046            Ovambo 1989-09-29                        NaN   

           haem: Laboratory haem: Laboratory text only  haem: RBC (x 10^12/L)  \
15              Taronga Zoo                        NaN                    NaN   
16              Taronga Zoo                        NaN                   4.40   
17              Taronga Zoo                        NaN                   3.30   
19              Taronga Zoo                        NaN                   6.00   
25  Orana Pathology Service                        NaN                   7.37   

   haem: haemoglobin (g/L)  haem: HCT (%)  \
15                      85           22.0   
16                      87           28.3   
17                      75           19.0   
19                     NaN           30.0   
25                     129           43.0   

    haem: Total Protein (refractometer)  haem: leukocyte count (x10^9/L)  \
15                                 83.0                             13.2   
16                                  NaN                              NaN   
17                                 80.0                             25.0   
19                                 92.0                              5.3   
25                                 75.0                             12.5   

    haem: neutrophils (%)  haem: neutrophils (band)  \
15                   98.0                       NaN   
16                   89.0                       NaN   
17                   99.0                       NaN   
19                   90.0                       NaN   
25                   66.0                       NaN   

    haem: neutrophils(seg) (x10^9/L)  haem: lymphocytes (x10^9/L)  \
15                               NaN                          NaN   
16                               NaN                          NaN   
17                               NaN                          NaN   
19                               NaN                          NaN   
25                               NaN                          NaN   

    haem: lymphocytes  (%)  haem: monocytes (x10^9/L)  haem: monocytes (%)  \
15                     2.0                        NaN                  NaN   
16                     5.0                        NaN                  4.0   
17                     NaN                        NaN                  1.0   
19                     7.0                        NaN                  1.0   
25                    21.0                        NaN                  1.0   

    haem: eosinophils  (x10^9/L)  haem: eosinophils (%)  \
15                           NaN                    NaN   
16                           NaN                    2.0   
17                           NaN                    NaN   
19                           NaN                    2.0   
25                           NaN                   12.0   

   haem: estimated platelets x 10^9/L (Hi)  \
15                                     NaN   
16                                     NaN   
17                                     NaN   
19                                     NaN   
25                                     352   

   haem: estimated platelets  /HPF (Low) haem: plasma sample appearance  \
15                                   NaN                            NaN   
16                                   NaN                            NaN   
17                                   NaN                            NaN   
19                                    10                            NaN   
25                                   NaN                            NaN   

    haem: 

In [14]:
# write to file
from datetime import datetime
today = datetime.today().strftime('%Y-%m-%d')
out_file = '../Data/big_cats/processed_data/merged_tables_tol_' +str(tol.days) +'days_' + today + '.csv'
everything.to_csv(out_file, index = False)

In [15]:
print('using a tolerance of: ' + str(tol))
print('there are total records: ' + str(len(everything)))
print('there are ' +str(len(triples)) + ' triple matches' )
print('there are ' +str(len(double_hb)) + ' double hb matches' )
print('there are ' +str(len(double_hu)) + ' double hu matches' )
print('there are ' +str(len(double_ub)) + ' double ub matches' )
print('there are ' +str(len(haem_singles)) + ' single haem records' )
print('there are ' +str(len(biochem_singles)) + ' single biochem records' )
print('there are ' +str(len(urine_singles)) + ' single urine records' )

using a tolerance of: 14 days 00:00:00
there are total records: 2355
there are 244 triple matches
there are 413 double hb matches
there are 3 double hu matches
there are 378 double ub matches
there are 60 single haem records
there are 673 single biochem records
there are 584 single urine records


using a tolerance of: 3 days 00:00:00
there are total records: 2388
there are 219 triple matches
there are 431 double hb matches
there are 5 double hu matches
there are 305 double ub matches
there are 65 single haem records
there are 695 single biochem records
there are 668 single urine records

using a tolerance of: 7 days 00:00:00
there are total records: 2369
there are 234 triple matches
there are 420 double hb matches
there are 3 double hu matches
there are 343 double ub matches
there are 63 single haem records
there are 683 single biochem records
there are 623 single urine records

using a tolerance of: 14 days 00:00:00
there are total records: 2355
there are 244 triple matches
there are 413 double hb matches
there are 3 double hu matches
there are 378 double ub matches
there are 60 single haem records
there are 673 single biochem records
there are 584 single urine records